In [161]:
import pandas as pd

from vcub_keeper.reader.reader_utils import filter_periode
from vcub_keeper.reader.reader import *
from vcub_keeper.visualisation import plot_station_activity
from vcub_keeper.transform.features_factory import *

import plotly.express as px
import matplotlib.pyplot as plt
import seaborn as sns
sns.set_style('whitegrid')
%matplotlib inline

%load_ext autoreload
%autoreload 2

pd.options.display.max_rows = 500

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


## Objectifs :

- Profilage des stations par leurs activités et fréquences
- On ne prend pas la période de confinement et les stations non utlisées par le grand public.
- Export d'un fichier de référence
- [Issue Github](https://github.com/armgilles/vcub_keeper/issues/28)

## Profilage des stations selon leurs activités et fréquence

In [114]:
# Lecture du fichier activité
ts_activity = read_time_serie_activity()

# Some features
ts_activity = get_transactions_in(ts_activity)
ts_activity = get_transactions_out(ts_activity)
ts_activity = get_transactions_all(ts_activity)
ts_activity = get_consecutive_no_transactions_out(ts_activity)

In [121]:
# Filter data with confinement & non use by consumer
ts_activity = filter_periode(ts_activity)

In [122]:
ts_activity.shape

(14952568, 9)

In [124]:
profile_station = \
    ts_activity[ts_activity['status'] == 1].groupby('station_id', 
                                                    as_index=False)['transactions_all'].agg({'total_point' : 'size',
                                                                                           'mean' : 'mean',
                                                                                           'median' : 'median',
                                                                                           'std' : 'std',
                                                                                           '95%': lambda x: x.quantile(0.95),
                                                                                           '98%': lambda x: x.quantile(0.98),
                                                                                           '99%': lambda x: x.quantile(0.99),
                                                                                           'max' : 'max'})
profile_station = profile_station.sort_values('mean')

On classe les stations suivant leurs moyennes d'activité (basé sur fréquence de 10 minutes)

In [125]:
profile_station['profile_station_activity'] = \
    pd.cut(profile_station['mean'], 3, labels=["low", "medium", "hight"])

In [126]:
profile_station = profile_station.round(2)

In [127]:
profile_station

station_id  total_point  mean  median   std  95%  98%   99%   max  \
180         181            2  0.00     0.0  0.00  0.0  0.0  0.00   0.0   
159         160        64496  0.00     0.0  0.07  0.0  0.0  0.00   5.0   
160         161        64028  0.01     0.0  0.10  0.0  0.0  0.00   6.0   
179         180        31672  0.01     0.0  0.12  0.0  0.0  0.00   8.0   
91           92        65219  0.01     0.0  0.12  0.0  0.0  0.00   6.0   
166         167        62437  0.01     0.0  0.14  0.0  0.0  0.00   9.0   
167         168        50066  0.01     0.0  0.13  0.0  0.0  1.00   6.0   
182         183        17277  0.01     0.0  0.14  0.0  0.0  1.00   5.0   
80           81        65125  0.02     0.0  0.16  0.0  0.0  1.00   8.0   
149         150        64702  0.02     0.0  0.16  0.0  0.0  1.00   9.0   
71           72        63991  0.02     0.0  0.18  0.0  0.0  1.00   7.0   
70           71        64813  0.02     0.0  0.19  0.0  0.0  1.00  10.0   
90           91        60429  0.02     0.0  0.18  0.0  0.0  1.00  11.0   
79           80        65157  0.02     0.0  0.17  0.0  0.0  1.00   9.0   
164         165        64788  0.02     0.0  0.17  0.0  0.0  1.00   7.0   
155         156        64896  0.02     0.0  0.20  0.0  1.0  1.00  10.0   
156         157        64322  0.03     0.0  0.21  0.0  1.0  1.00  11.0   
86           87        64712  0.03     0.0  0.22  0.0  1.0  1.00   9.0   
181         182        17182  0.03     0.0  0.23  0.0  1.0  1.00  10.0   
92           93        64626  0.03     0.0  0.23  0.0  1.0  1.00  11.0   
93           94        64858  0.03     0.0  0.23  0.0  1.0  1.00  13.0   
148         149        64644  0.04     0.0  0.24  0.0  1.0  1.00  15.0   
81           82        64362  0.04     0.0  0.24  0.0  1.0  1.00  11.0   
87           88        64014  0.05     0.0  0.26  0.0  1.0  1.00  13.0   
163         164        65159  0.05     0.0  0.26  0.0  1.0  1.00   8.0   
75           76        60181  0.05     0.0  0.31  0.0  1.0  1.00  13.0   
76           77        65000  0.05     0.0  0.29  0.0  1.0  1.00  11.0   
157         158        64071  0.05     0.0  0.28  0.0  1.0  1.00  11.0   
147         148        64512  0.05     0.0  0.29  0.0  1.0  1.00   8.0   
78           79        65023  0.05     0.0  0.27  0.0  1.0  1.00  12.0   
94           95        64389  0.05     0.0  0.28  0.0  1.0  1.00   8.0   
150         151        64909  0.05     0.0  0.39  0.0  1.0  1.00  14.0   
85           86        64827  0.06     0.0  0.29  0.0  1.0  1.00  10.0   
152         153        64875  0.06     0.0  0.30  0.0  1.0  1.00   9.0   
158         159        65066  0.06     0.0  0.34  0.0  1.0  2.00  11.0   
84           85        64502  0.06     0.0  0.29  1.0  1.0  1.00  10.0   
161         162        63648  0.06     0.0  0.37  0.0  1.0  1.00  13.0   
168         169        63591  0.07     0.0  0.32  1.0  1.0  1.00  11.0   
176         177        32005  0.07     0.0  0.34  1.0  1.0  1.00  11.0   
77           78        63997  0.07     0.0  0.32  1.0  1.0  1.00  13.0   
146         147        64476  0.07     0.0  0.38  1.0  1.0  1.00  12.0   
96           97        65094  0.07     0.0  0.38  1.0  1.0  1.00  12.0   
83           84        63246  0.08     0.0  0.37  1.0  1.0  1.00  12.0   
162         163        64663  0.08     0.0  0.41  1.0  1.0  1.00  13.0   
62           63        64525  0.09     0.0  0.41  1.0  1.0  2.00  10.0   
145         146        63337  0.09     0.0  0.43  1.0  1.0  2.00  19.0   
165         166        63470  0.10     0.0  0.42  1.0  1.0  2.00  12.0   
88           89        65109  0.10     0.0  0.36  1.0  1.0  1.00  10.0   
151         152        64908  0.10     0.0  0.40  1.0  1.0  1.00  11.0   
142         143        61131  0.10     0.0  0.39  1.0  1.0  1.92  13.0   
114         115        63745  0.10     0.0  0.41  1.0  1.0  1.00  15.0   
141         142        64838  0.11     0.0  0.39  1.0  1.0  2.00  11.0   
63           64        64632  0.11     0.0  0.39  1.0  1.0  2.00  14.0   
73       

In [128]:
profile_station.profile_station_activity.value_counts()

low       128
medium     50
hight       6
Name: profile_station_activity, dtype: int64

In [36]:
fig = px.box(profile_station, x="profile_station_activity", y="mean",
            points='all',
            color='profile_station_activity',
            hover_data=['total_point', 'mean', '95%', 'std'],
            labels={'profile_station_activity' : 'Profile activité'},
            boxmode='group')
fig.show()

In [49]:
## Export
profile_station[['station_id', 
                 'profile_station_activity']].to_csv(ROOT_DATA_REF+'station_profile.csv',
                                                     index=False, encoding='utf-8')

## Industrialisation

In [130]:
def create_station_profilage_activity():
    """
    Création d'un fichier classifiant les stations suivant leurs activités et 
    leurs fréquences d'utilation (données filtré par reader_utils.py filter_periode() )
    Création du fichier `station_profile.csv` dans ROOT_DATA_REF

    Parameters
    ----------
    None
    
    Returns
    -------
    None
        
    Examples
    --------
    
    create_station_profilage_activity()
    """
    
    # Lecture du fichier activité
    ts_activity = read_time_serie_activity()

    # Some features
    ts_activity = get_transactions_in(ts_activity)
    ts_activity = get_transactions_out(ts_activity)
    ts_activity = get_transactions_all(ts_activity)
    ts_activity = get_consecutive_no_transactions_out(ts_activity)
    
    # Filter data with confinement & non use by consumer
    ts_activity = filter_periode(ts_activity)
    
    # Aggrégation de l'activité par stations
    profile_station = \
        ts_activity[ts_activity['status'] == 1].groupby('station_id', 
                                                        as_index=False)['transactions_all'].agg({'total_point' : 'size',
                                                                                                 'mean' : 'mean',
                                                                                                 'median' : 'median',
                                                                                                 'std' : 'std',
                                                                                                 '95%': lambda x: x.quantile(0.95),
                                                                                                 '98%': lambda x: x.quantile(0.98),
                                                                                                 '99%': lambda x: x.quantile(0.99),
                                                                                                 'max' : 'max'})
    profile_station = profile_station.sort_values('mean')
    # Classification en 3 activités (low / medium / hight)
    profile_station['profile_station_activity'] = \
        pd.cut(profile_station['mean'], 3, labels=["low", "medium", "high"])
    
    ## Export
    profile_station.to_csv(ROOT_DATA_REF+'station_profile.csv',
                                                         index=False, encoding='utf-8')

In [131]:
def read_station_profile(file_name='station_profile.csv'):
    """
    Lecture du fichier sur qui classifie les stations par rapport à leurs activité et 
    fréquences d'utilisation.
    Ce fichier est situé dans ROOT_DATA_REF
    
    Parameters
    ----------
    file_name : str
        Nom du fichier
    
    Returns
    -------
    station_profile : DataFrame
        
    Examples
    --------
    
    station_profile = read_station_profile()
    """
    station_profile = pd.read_csv(ROOT_DATA_REF+file_name, sep=',')
    
    return station_profile
    

In [162]:
from vcub_keeper.reader.reader import read_station_profile
from vcub_keeper.create.creator import create_station_profilage_activity

In [156]:
create_station_profilage_activity()

In [157]:
station_profile = read_station_profile()

In [158]:
station_profile

station_id  total_point      mean  median       std  95%  98%   99%  \
0           181            2  0.000000     0.0  0.000000  0.0  0.0  0.00   
1           160        64496  0.002807     0.0  0.066428  0.0  0.0  0.00   
2           161        64028  0.006937     0.0  0.100847  0.0  0.0  0.00   
3           180        31672  0.007359     0.0  0.121230  0.0  0.0  0.00   
4            92        65219  0.008589     0.0  0.118351  0.0  0.0  0.00   
5           167        62437  0.009597     0.0  0.139767  0.0  0.0  0.00   
6           168        50066  0.012568     0.0  0.132083  0.0  0.0  1.00   
7           183        17277  0.012852     0.0  0.136782  0.0  0.0  1.00   
8            81        65125  0.015591     0.0  0.163543  0.0  0.0  1.00   
9           150        64702  0.015693     0.0  0.155258  0.0  0.0  1.00   
10           72        63991  0.019557     0.0  0.178955  0.0  0.0  1.00   
11           71        64813  0.019710     0.0  0.186596  0.0  0.0  1.00   
12           91        60429  0.019815     0.0  0.184904  0.0  0.0  1.00   
13           80        65157  0.020112     0.0  0.171139  0.0  0.0  1.00   
14          165        64788  0.022404     0.0  0.173097  0.0  0.0  1.00   
15          156        64896  0.024432     0.0  0.197651  0.0  1.0  1.00   
16          157        64322  0.025895     0.0  0.212369  0.0  1.0  1.00   
17           87        64712  0.026589     0.0  0.215363  0.0  1.0  1.00   
18          182        17182  0.028234     0.0  0.234343  0.0  1.0  1.00   
19           93        64626  0.028621     0.0  0.226151  0.0  1.0  1.00   
20           94        64858  0.029213     0.0  0.233360  0.0  1.0  1.00   
21          149        64644  0.037187     0.0  0.244142  0.0  1.0  1.00   
22           82        64362  0.042602     0.0  0.242011  0.0  1.0  1.00   
23           88        64014  0.045163     0.0  0.261132  0.0  1.0  1.00   
24          164        65159  0.045167     0.0  0.263052  0.0  1.0  1.00   
25           76        60181  0.045264     0.0  0.313218  0.0  1.0  1.00   
26           77        65000  0.047478     0.0  0.290688  0.0  1.0  1.00   
27          158        64071  0.048276     0.0  0.282483  0.0  1.0  1.00   
28          148        64512  0.049498     0.0  0.286304  0.0  1.0  1.00   
29           79        65023  0.049507     0.0  0.272896  0.0  1.0  1.00   
30           95        64389  0.050197     0.0  0.278905  0.0  1.0  1.00   
31          151        64909  0.053618     0.0  0.392710  0.0  1.0  1.00   
32           86        64827  0.055399     0.0  0.292946  0.0  1.0  1.00   
33          153        64875  0.057947     0.0  0.299425  0.0  1.0  1.00   
34          159        65066  0.058777     0.0  0.342735  0.0  1.0  2.00   
35           85        64502  0.059416     0.0  0.293267  1.0  1.0  1.00   
36          162        63648  0.060382     0.0  0.367902  0.0  1.0  1.00   
37          169        63591  0.067707     0.0  0.323553  1.0  1.0  1.00   
38          177        32005  0.069142     0.0  0.341783  1.0  1.0  1.00   
39           78        63997  0.070214     0.0  0.316798  1.0  1.0  1.00   
40          147        64476  0.073295     0.0  0.377193  1.0  1.0  1.00   
41           97        65094  0.073951     0.0  0.378504  1.0  1.0  1.00   
42           84        63246  0.083876     0.0  0.365937  1.0  1.0  1.00   
43          163        64663  0.084220     0.0  0.414199  1.0  1.0  1.00   
44           63        64525  0.090726     0.0  0.408228  1.0  1.0  2.00   
45          146        63337  0.091733     0.0  0.425470  1.0  1.0  2.00   
46          166        63470  0.097183     0.0  0.417570  1.0  1.0  2.00   
47           89        65109  0.099637     0.0  0.363141  1.0  1.0  1.00   
48          152        64908  0.100902     0.0  0.396380  1.0  1.0  1.00   
49          143        61131  0.101949     0.0  0.389461  1.0  1.0  1.92   
50          115        63745  0.104560     0.0  0.413212  1.0  1.0  1.00   
51          142        64838  0.107492     0.0  0.385

### Analyse de l'activité des stations :

In [163]:
# Lecture du profile activité des stations
station_profile = read_station_profile()

# lecture des attributs des stations
stations = read_stations_attributes()

In [164]:
station_profile.profile_station_activity.value_counts()

low       128
medium     50
high        6
Name: profile_station_activity, dtype: int64

In [165]:
# Filtrage des colonnes
stations = stations[['station_id', 'COMMUNE', 'NOM']]

In [166]:
station_profile = station_profile.merge(stations, on='station_id', how='left')

In [167]:
station_profile

station_id  total_point      mean  median       std  95%  98%   99%  \
0           181            2  0.000000     0.0  0.000000  0.0  0.0  0.00   
1           160        64496  0.002807     0.0  0.066428  0.0  0.0  0.00   
2           161        64028  0.006937     0.0  0.100847  0.0  0.0  0.00   
3           180        31672  0.007359     0.0  0.121230  0.0  0.0  0.00   
4            92        65219  0.008589     0.0  0.118351  0.0  0.0  0.00   
5           167        62437  0.009597     0.0  0.139767  0.0  0.0  0.00   
6           168        50066  0.012568     0.0  0.132083  0.0  0.0  1.00   
7           183        17277  0.012852     0.0  0.136782  0.0  0.0  1.00   
8            81        65125  0.015591     0.0  0.163543  0.0  0.0  1.00   
9           150        64702  0.015693     0.0  0.155258  0.0  0.0  1.00   
10           72        63991  0.019557     0.0  0.178955  0.0  0.0  1.00   
11           71        64813  0.019710     0.0  0.186596  0.0  0.0  1.00   
12           91        60429  0.019815     0.0  0.184904  0.0  0.0  1.00   
13           80        65157  0.020112     0.0  0.171139  0.0  0.0  1.00   
14          165        64788  0.022404     0.0  0.173097  0.0  0.0  1.00   
15          156        64896  0.024432     0.0  0.197651  0.0  1.0  1.00   
16          157        64322  0.025895     0.0  0.212369  0.0  1.0  1.00   
17           87        64712  0.026589     0.0  0.215363  0.0  1.0  1.00   
18          182        17182  0.028234     0.0  0.234343  0.0  1.0  1.00   
19           93        64626  0.028621     0.0  0.226151  0.0  1.0  1.00   
20           94        64858  0.029213     0.0  0.233360  0.0  1.0  1.00   
21          149        64644  0.037187     0.0  0.244142  0.0  1.0  1.00   
22           82        64362  0.042602     0.0  0.242011  0.0  1.0  1.00   
23           88        64014  0.045163     0.0  0.261132  0.0  1.0  1.00   
24          164        65159  0.045167     0.0  0.263052  0.0  1.0  1.00   
25           76        60181  0.045264     0.0  0.313218  0.0  1.0  1.00   
26           77        65000  0.047478     0.0  0.290688  0.0  1.0  1.00   
27          158        64071  0.048276     0.0  0.282483  0.0  1.0  1.00   
28          148        64512  0.049498     0.0  0.286304  0.0  1.0  1.00   
29           79        65023  0.049507     0.0  0.272896  0.0  1.0  1.00   
30           95        64389  0.050197     0.0  0.278905  0.0  1.0  1.00   
31          151        64909  0.053618     0.0  0.392710  0.0  1.0  1.00   
32           86        64827  0.055399     0.0  0.292946  0.0  1.0  1.00   
33          153        64875  0.057947     0.0  0.299425  0.0  1.0  1.00   
34          159        65066  0.058777     0.0  0.342735  0.0  1.0  2.00   
35           85        64502  0.059416     0.0  0.293267  1.0  1.0  1.00   
36          162        63648  0.060382     0.0  0.367902  0.0  1.0  1.00   
37          169        63591  0.067707     0.0  0.323553  1.0  1.0  1.00   
38          177        32005  0.069142     0.0  0.341783  1.0  1.0  1.00   
39           78        63997  0.070214     0.0  0.316798  1.0  1.0  1.00   
40          147        64476  0.073295     0.0  0.377193  1.0  1.0  1.00   
41           97        65094  0.073951     0.0  0.378504  1.0  1.0  1.00   
42           84        63246  0.083876     0.0  0.365937  1.0  1.0  1.00   
43          163        64663  0.084220     0.0  0.414199  1.0  1.0  1.00   
44           63        64525  0.090726     0.0  0.408228  1.0  1.0  2.00   
45          146        63337  0.091733     0.0  0.425470  1.0  1.0  2.00   
46          166        63470  0.097183     0.0  0.417570  1.0  1.0  2.00   
47           89        65109  0.099637     0.0  0.363141  1.0  1.0  1.00   
48          152        64908  0.100902     0.0  0.396380  1.0  1.0  1.00   
49          143        61131  0.101949     0.0  0.389461  1.0  1.0  1.92   
50          115        63745  0.104560     0.0  0.413212  1.0  1.0  1.00   
51          142        64838  0.107492     0.0  0.385

In [168]:
station_profile[station_profile.station_id >= 175].sort_values('station_id')

station_id  total_point      mean  median       std  95%  98%  99%   max  \
64         175        64701  0.144125     0.0  0.485897  1.0  1.0  2.0  14.0   
82         176        59468  0.205985     0.0  0.583721  1.0  2.0  2.0  15.0   
38         177        32005  0.069142     0.0  0.341783  1.0  1.0  1.0  11.0   
65         178        58755  0.162384     0.0  0.537831  1.0  2.0  2.0  14.0   
93         179        59095  0.234955     0.0  0.620703  1.0  2.0  2.0  14.0   
3          180        31672  0.007359     0.0  0.121230  0.0  0.0  0.0   8.0   
0          181            2  0.000000     0.0  0.000000  0.0  0.0  0.0   0.0   
18         182        17182  0.028234     0.0  0.234343  0.0  1.0  1.0  10.0   
7          183        17277  0.012852     0.0  0.136782  0.0  0.0  1.0   5.0   
60         251        10033  0.132715     0.0  0.563336  1.0  2.0  2.0  15.0   

   profile_station_activity COMMUNE  NOM  
64                      low     NaN  NaN  
82                      low     NaN  NaN  
38                      low     NaN  NaN  
65                      low     NaN  NaN  
93                      low     NaN  NaN  
3                       low     NaN  NaN  
0                       low     NaN  NaN  
18                      low     NaN  NaN  
7                       low     NaN  NaN  
60                      low     NaN  NaN

In [169]:
station_profile = station_profile.round(2)

In [170]:
fig = px.box(station_profile, x="profile_station_activity", y="mean",
            points='all',
            color='profile_station_activity',
            hover_data=['station_id','NOM', 'total_point', 'mean', '95%', 'std', 'COMMUNE'],
            labels={'profile_station_activity' : 'Profile activité',
                    'NOM' : 'Nom',
                    'COMMUNE' : 'Commune'},
            boxmode='group')
fig.show()

In [154]:
station_profile

station_id  total_point  mean  median   std  95%  98%   99%   max  \
0           181            2  0.00     0.0  0.00  0.0  0.0  0.00   0.0   
1           160        64496  0.00     0.0  0.07  0.0  0.0  0.00   5.0   
2           161        64028  0.01     0.0  0.10  0.0  0.0  0.00   6.0   
3           180        31672  0.01     0.0  0.12  0.0  0.0  0.00   8.0   
4            92        65219  0.01     0.0  0.12  0.0  0.0  0.00   6.0   
5           167        62437  0.01     0.0  0.14  0.0  0.0  0.00   9.0   
6           168        50066  0.01     0.0  0.13  0.0  0.0  1.00   6.0   
7           183        17277  0.01     0.0  0.14  0.0  0.0  1.00   5.0   
8            81        65125  0.02     0.0  0.16  0.0  0.0  1.00   8.0   
9           150        64702  0.02     0.0  0.16  0.0  0.0  1.00   9.0   
10           72        63991  0.02     0.0  0.18  0.0  0.0  1.00   7.0   
11           71        64813  0.02     0.0  0.19  0.0  0.0  1.00  10.0   
12           91        60429  0.02     0.0  0.18  0.0  0.0  1.00  11.0   
13           80        65157  0.02     0.0  0.17  0.0  0.0  1.00   9.0   
14          165        64788  0.02     0.0  0.17  0.0  0.0  1.00   7.0   
15          156        64896  0.02     0.0  0.20  0.0  1.0  1.00  10.0   
16          157        64322  0.03     0.0  0.21  0.0  1.0  1.00  11.0   
17           87        64712  0.03     0.0  0.22  0.0  1.0  1.00   9.0   
18          182        17182  0.03     0.0  0.23  0.0  1.0  1.00  10.0   
19           93        64626  0.03     0.0  0.23  0.0  1.0  1.00  11.0   
20           94        64858  0.03     0.0  0.23  0.0  1.0  1.00  13.0   
21          149        64644  0.04     0.0  0.24  0.0  1.0  1.00  15.0   
22           82        64362  0.04     0.0  0.24  0.0  1.0  1.00  11.0   
23           88        64014  0.05     0.0  0.26  0.0  1.0  1.00  13.0   
24          164        65159  0.05     0.0  0.26  0.0  1.0  1.00   8.0   
25           76        60181  0.05     0.0  0.31  0.0  1.0  1.00  13.0   
26           77        65000  0.05     0.0  0.29  0.0  1.0  1.00  11.0   
27          158        64071  0.05     0.0  0.28  0.0  1.0  1.00  11.0   
28          148        64512  0.05     0.0  0.29  0.0  1.0  1.00   8.0   
29           79        65023  0.05     0.0  0.27  0.0  1.0  1.00  12.0   
30           95        64389  0.05     0.0  0.28  0.0  1.0  1.00   8.0   
31          151        64909  0.05     0.0  0.39  0.0  1.0  1.00  14.0   
32           86        64827  0.06     0.0  0.29  0.0  1.0  1.00  10.0   
33          153        64875  0.06     0.0  0.30  0.0  1.0  1.00   9.0   
34          159        65066  0.06     0.0  0.34  0.0  1.0  2.00  11.0   
35           85        64502  0.06     0.0  0.29  1.0  1.0  1.00  10.0   
36          162        63648  0.06     0.0  0.37  0.0  1.0  1.00  13.0   
37          169        63591  0.07     0.0  0.32  1.0  1.0  1.00  11.0   
38          177        32005  0.07     0.0  0.34  1.0  1.0  1.00  11.0   
39           78        63997  0.07     0.0  0.32  1.0  1.0  1.00  13.0   
40          147        64476  0.07     0.0  0.38  1.0  1.0  1.00  12.0   
41           97        65094  0.07     0.0  0.38  1.0  1.0  1.00  12.0   
42           84        63246  0.08     0.0  0.37  1.0  1.0  1.00  12.0   
43          163        64663  0.08     0.0  0.41  1.0  1.0  1.00  13.0   
44           63        64525  0.09     0.0  0.41  1.0  1.0  2.00  10.0   
45          146        63337  0.09     0.0  0.43  1.0  1.0  2.00  19.0   
46          166        63470  0.10     0.0  0.42  1.0  1.0  2.00  12.0   
47           89        65109  0.10     0.0  0.36  1.0  1.0  1.00  10.0   
48          152        64908  0.10     0.0  0.40  1.0  1.0  1.00  11.0   
49          143        61131  0.10     0.0  0.39  1.0  1.0  1.92  13.0   
50          115        63745  0.10     0.0  0.41  1.0  1.0  1.00  15.0   
51          142        64838  0.11     0.0  0.39  1.0  1.0  2.00  11.0   
52           64        64632  0.11     0.0  0.39  1.0  1.0  2.00  14.0   
53       

In [152]:
station_id = 174
plot_station_activity(ts_activity, station_id=station_id, 
                      features_to_plot=['transactions_all'],
                      #start_date=start_date,
                      #end_date=end_date,
                      return_data=False
                     )